# Benchmarking skforecast

This notebook benchmarks the performance (velocity) of the `skforecast` in its different versions and keeps track of the results.

**Notes**

+ In version `0.15.0` the binning of residuals was introduced in multi-series forecasters. This explains the increase in the time taken to fit the model.

In [1]:
%load_ext autoreload
%autoreload 2
import sys
from pathlib import Path
path = str(Path.cwd().parent)
print(path)
sys.path.insert(1, path)

c:\Users\jaesc2\GitHub\skforecast


In [2]:
# !pip install --upgrade numpy < 2.0 && \
# pip install --upgrade pandas && \
# pip install --upgrade scikit-learn

In [3]:
# !pip install skforecast==0.15.1
# !pip install skforecast==0.14.0
# !pip install skforecast==0.13.0

In [2]:
# Libraries
# ==============================================================================
import numpy as np
import pandas as pd
import sklearn
import joblib
from benchmarking import BenchmarkRunner, plot_benchmark_results
import skforecast
import platform
import psutil
import plotly.express as px
from sklearn.preprocessing import StandardScaler
from sklearn.linear_model import LinearRegression
from lightgbm import LGBMRegressor

from skforecast.utils import *
if skforecast.__version__ >= '0.14.0':
    from skforecast.recursive import ForecasterRecursive, ForecasterRecursiveMultiSeries
    from skforecast.direct import ForecasterDirect, ForecasterDirectMultiVariate
    from skforecast.model_selection import TimeSeriesFold, backtesting_forecaster, backtesting_forecaster_multiseries
else:
    from skforecast.ForecasterAutoreg import ForecasterAutoreg
    from skforecast.ForecasterAutoregMultiSeries import ForecasterAutoregMultiSeries
    from skforecast.ForecasterAutoregDirect import ForecasterAutoregDirect
    from skforecast.ForecasterAutoregMultiVariate import ForecasterAutoregMultiVariate
    from skforecast.model_selection import backtesting_forecaster, backtesting_forecaster_multiseries

In [3]:
print(f"Python version: {platform.python_version()}")
print(f"skforecast version: {skforecast.__version__}")
print(f"scikit-learn version: {sklearn.__version__}")
print(f"pandas version: {pd.__version__}")
print(f"numpy version: {np.__version__}")
print(f"Computer network name: {platform.node()}")
print(f"Processor type: {platform.processor()}")
print(f"Platform type: {platform.platform()}")
print(f"Operating system: {platform.system()}")
print(f"Operating system release: {platform.release()}")
print(f"Operating system version: {platform.version()}")
print(f"Number of physical cores: {psutil.cpu_count(logical=False)}")
print(f"Number of logical cores: {psutil.cpu_count(logical=True)}")

Python version: 3.11.10
skforecast version: 0.16.0
scikit-learn version: 1.6.1
pandas version: 2.2.3
numpy version: 2.2.5
Computer network name: ITES015-NB0029
Processor type: Intel64 Family 6 Model 141 Stepping 1, GenuineIntel
Platform type: Windows-10-10.0.19045-SP0
Operating system: Windows
Operating system release: 10
Operating system version: 10.0.19045
Number of physical cores: 8
Number of logical cores: 16


# ForecasterRecursiveMultiSeries

In [4]:
# Mock data for benchmarking
# ==========================================================
n_series = 600
len_series = 2000
series_dict = {}
rng = np.random.default_rng(321)
for i in range(n_series):
    series_dict[f'series_{i}'] = pd.Series(
        data = rng.normal(loc=20, scale=5, size=len_series),
        index=pd.date_range(
            start='2010-01-01',
            periods=len_series,
            freq='h'
        ),
        name=f'series_{i}'
    )
series_dataframe = pd.DataFrame(series_dict, index=series_dict['series_0'].index)

exog_dict = {}
rng = np.random.default_rng(321)
for k in series_dict.keys():
    exog = pd.DataFrame(
            index=series_dict[k].index
            )
    exog['day_of_week'] = exog.index.dayofweek
    exog['week_of_year'] = exog.index.isocalendar().week.astype(int)
    exog['month'] = exog.index.month
    exog_dict[k] = exog

exog_dict_prediction = {}
for k in series_dict.keys():
    exog = pd.DataFrame(
            index=pd.date_range(
                start=series_dict[k].index.max() + pd.Timedelta(hours=1),
                periods=100,
                freq='h'
            )
            )
    exog['day_of_week'] = exog.index.dayofweek
    exog['week_of_year'] = exog.index.isocalendar().week.astype(int)
    exog['month'] = exog.index.month
    exog_dict_prediction[k] = exog

In [ ]:
# Benchmarking speed ForecasterRecursiveMultiSeries
# ==============================================================================
regressor = LGBMRegressor(random_state=8520, verbose=-1)
# regressor = LinearRegression()
if skforecast.__version__ >= '0.14.0':
    forecaster = ForecasterRecursiveMultiSeries(
        regressor=regressor,
        lags=50,
        transformer_series=StandardScaler(),
        transformer_exog=StandardScaler(),
        encoding="ordinal"
    )
else:
    forecaster = ForecasterAutoregMultiSeries(
        regressor=regressor,
        lags=50,
        transformer_series=StandardScaler(),
        transformer_exog=StandardScaler(),
        encoding="ordinal"
    )

def ForecasterRecursiveMultiSeries_fit_series_is_dict_exog_is_dict():
    forecaster.fit(series=series_dict, exog=exog_dict)

def ForecasterRecursiveMultiSeries__create_train_X_y_series_is_dict_exog_is_dict():
    forecaster._create_train_X_y(series=series_dict, exog=exog_dict)

def ForecasterRecursiveMultiSeries_fit_series_is_dataframe_no_exog():
    forecaster.fit(series=series_dataframe)

def ForecasterRecursiveMultiSeries__create_train_X_y_series_is_dataframe_no_exog():
    forecaster._create_train_X_y(series=series_dataframe)

def ForecasterRecursiveMultiSeries__create_train_X_y_series_is_dataframe_exog_dict():
    forecaster._create_train_X_y(series=series_dataframe, exog=exog_dict)

def ForecasterRecursiveMultiSeries__create_train_X_y_single_series():
    _ = forecaster._create_train_X_y_single_series(
            y = series_dict['series_0'],
            exog = exog_dict['series_0'],
            ignore_exog = False,
        )

def ForecasterRecursiveMultiSeries_predict_exog_is_dict():
    forecaster.predict(steps=100, exog=exog_dict_prediction, suppress_warnings=True)

def ForecasterRecursiveMultiSeries__create_predict_inputs_exog_is_dict():
    _ = forecaster._create_predict_inputs(
            steps         = 100,
            exog         = exog_dict_prediction,
            check_inputs = True
        )

def ForecasterRecursiveMultiSeries__check_predict_inputs():
    check_predict_input(
        forecaster_name  = type(forecaster).__name__,
        steps            = 100,
        is_fitted        = forecaster.is_fitted,
        exog_in_         = forecaster.exog_in_,
        index_type_      = forecaster.index_type_,
        index_freq_      = forecaster.index_freq_,
        window_size      = forecaster.window_size,
        last_window      = pd.DataFrame(forecaster.last_window_),
        exog             = exog_dict_prediction,
        exog_type_in_    = forecaster.exog_type_in_,
        exog_names_in_   = forecaster.exog_names_in_,
        interval         = None,
        levels           = forecaster.series_names_in_,
        series_names_in_ = forecaster.series_names_in_,
        encoding         = forecaster.encoding
    )

def ForecasterRecursiveMultiSeries_backtesting_series_is_dict_exog_is_dict():
    if skforecast.__version__ >= '0.14.0':
        cv = TimeSeriesFold(
                initial_train_size=1200,
                fixed_train_size=True,
                steps=50,
            )
        _ = backtesting_forecaster_multiseries(
                forecaster=forecaster,
                series=series_dict,
                exog=exog_dict,
                cv=cv,
                metric='mean_squared_error',
                show_progress=False
            )
    else:
        _ = backtesting_forecaster_multiseries(
                forecaster=forecaster,
                series=series_dict,
                exog=exog_dict,
                initial_train_size=1200,
                fixed_train_size=True,
                steps=50,
                metric='mean_squared_error',
                show_progress=False
            )
        
def ForecasterRecursiveMultiSeries_backtesting_series_is_dataframe_no_exog():
    if skforecast.__version__ >= '0.14.0':
        cv = TimeSeriesFold(
                initial_train_size=1200,
                fixed_train_size=True,
                steps=50,
            )
        _ = backtesting_forecaster_multiseries(
                forecaster=forecaster,
                series=series_dataframe,
                cv=cv,
                metric='mean_squared_error',
                show_progress=False
            )
    else:
        _ = backtesting_forecaster_multiseries(
                forecaster=forecaster,
                series=series_dataframe,
                initial_train_size=1200,
                fixed_train_size=True,
                steps=50,
                metric='mean_squared_error',
                show_progress=False
            )
        
def ForecasterRecursiveMultiSeries_backtesting_series_is_dataframe_exog_dict():
    if skforecast.__version__ >= '0.14.0':
        cv = TimeSeriesFold(
                initial_train_size=1200,
                fixed_train_size=True,
                steps=50,
            )
        _ = backtesting_forecaster_multiseries(
                forecaster=forecaster,
                series=series_dataframe,
                exog=exog_dict,
                cv=cv,
                metric='mean_squared_error',
                show_progress=False
            )
    else:
        _ = backtesting_forecaster_multiseries(
                forecaster=forecaster,
                series=series_dataframe,
                exog=exog_dict,
                initial_train_size=1200,
                fixed_train_size=True,
                steps=50,
                metric='mean_squared_error',
                show_progress=False
            )


runner = BenchmarkRunner(repeat=10, output_dir="./")
_ = runner.benchmark(ForecasterRecursiveMultiSeries__create_train_X_y_series_is_dict_exog_is_dict, forecaster= forecaster)
_ = runner.benchmark(ForecasterRecursiveMultiSeries__create_train_X_y_series_is_dataframe_no_exog, forecaster= forecaster)
_ = runner.benchmark(ForecasterRecursiveMultiSeries__create_train_X_y_series_is_dataframe_exog_dict, forecaster= forecaster)

runner = BenchmarkRunner(repeat=5, output_dir="./")
_ = runner.benchmark(ForecasterRecursiveMultiSeries_fit_series_is_dict_exog_is_dict, forecaster= forecaster)
_ = runner.benchmark(ForecasterRecursiveMultiSeries_fit_series_is_dataframe_no_exog, forecaster= forecaster)

forecaster.fit(series=series_dict, exog=exog_dict)
runner = BenchmarkRunner(repeat=10, output_dir="./")
_ = runner.benchmark(ForecasterRecursiveMultiSeries__create_train_X_y_single_series, forecaster= forecaster)
_ = runner.benchmark(ForecasterRecursiveMultiSeries_predict_exog_is_dict, forecaster= forecaster)
_ = runner.benchmark(ForecasterRecursiveMultiSeries__create_predict_inputs_exog_is_dict, forecaster= forecaster)
_ = runner.benchmark(ForecasterRecursiveMultiSeries__check_predict_inputs, forecaster= forecaster)

runner = BenchmarkRunner(repeat=5, output_dir="./")
_ = runner.benchmark(ForecasterRecursiveMultiSeries_backtesting_series_is_dict_exog_is_dict, forecaster= forecaster)
_ = runner.benchmark(ForecasterRecursiveMultiSeries_backtesting_series_is_dataframe_no_exog, forecaster= forecaster)
_ = runner.benchmark(ForecasterRecursiveMultiSeries_backtesting_series_is_dataframe_exog_dict, forecaster= forecaster)

Benchmarking function: ForecasterRecursiveMultiSeries_fit_series_is_dict_exog_is_dict with skforecast version 0.16.0
Benchmarking function: ForecasterRecursiveMultiSeries__create_train_X_y_series_is_dict_exog_is_dict with skforecast version 0.16.0
Benchmarking function: ForecasterRecursiveMultiSeries_fit_series_is_dataframe_no_exog with skforecast version 0.16.0
Benchmarking function: ForecasterRecursiveMultiSeries__create_train_X_y_series_is_dataframe_no_exog with skforecast version 0.16.0
Benchmarking function: ForecasterRecursiveMultiSeries__create_train_X_y_single_series with skforecast version 0.16.0


c:\Users\jaesc2\Miniconda3\envs\skforecast_py11_2\Lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
c:\Users\jaesc2\Miniconda3\envs\skforecast_py11_2\Lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
c:\Users\jaesc2\Miniconda3\envs\skforecast_py11_2\Lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
c:\Users\jaesc2\Miniconda3\envs\skforecast_py11_2\Lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
c:\Users\jaesc2\Miniconda3\envs\skforecast_py11_2\Lib\site-packages\sklearn\utils\deprecation.py:151: Future

Benchmarking function: ForecasterRecursiveMultiSeries_predict_exog_is_dict with skforecast version 0.16.0
Benchmarking function: ForecasterRecursiveMultiSeries__create_predict_inputs_exog_is_dict with skforecast version 0.16.0
Benchmarking function: ForecasterRecursiveMultiSeries__check_predict_inputs with skforecast version 0.16.0


c:\Users\jaesc2\Miniconda3\envs\skforecast_py11_2\Lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
c:\Users\jaesc2\Miniconda3\envs\skforecast_py11_2\Lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
c:\Users\jaesc2\Miniconda3\envs\skforecast_py11_2\Lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
c:\Users\jaesc2\Miniconda3\envs\skforecast_py11_2\Lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
c:\Users\jaesc2\Miniconda3\envs\skforecast_py11_2\Lib\site-packages\sklearn\utils\deprecation.py:151: Future

Benchmarking function: ForecasterRecursiveMultiSeries_backtesting_series_is_dict_exog_is_dict with skforecast version 0.16.0


c:\Users\jaesc2\Miniconda3\envs\skforecast_py11_2\Lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
c:\Users\jaesc2\Miniconda3\envs\skforecast_py11_2\Lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
c:\Users\jaesc2\Miniconda3\envs\skforecast_py11_2\Lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
c:\Users\jaesc2\Miniconda3\envs\skforecast_py11_2\Lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
c:\Users\jaesc2\Miniconda3\envs\skforecast_py11_2\Lib\site-packages\sklearn\utils\deprecation.py:151: Future

Benchmarking function: ForecasterRecursiveMultiSeries_backtesting_series_is_dataframe_no_exog with skforecast version 0.16.0


In [5]:
# Plot results
# ==============================================================================
results_benchmark_all = joblib.load("./benchmark.joblib")
results_benchmark = results_benchmark_all.query("forecaster_name in ['ForecasterRecursiveMultiSeries', 'ForecasterAutoregMultiSeries']").copy()
results_benchmark = results_benchmark.query("regressor_name == 'LGBMRegressor'").copy()
for function_name in results_benchmark['function_name'].unique():
    df = results_benchmark.query(f"function_name == '{function_name}'").copy()
    display(df)
    plot_benchmark_results(df, function_name)

forecaster_name regressor_name  \
0    ForecasterRecursiveMultiSeries  LGBMRegressor   
12   ForecasterRecursiveMultiSeries  LGBMRegressor   
24   ForecasterRecursiveMultiSeries  LGBMRegressor   
36     ForecasterAutoregMultiSeries  LGBMRegressor   
48     ForecasterAutoregMultiSeries  LGBMRegressor   
68   ForecasterRecursiveMultiSeries  LGBMRegressor   
80   ForecasterRecursiveMultiSeries  LGBMRegressor   
92   ForecasterRecursiveMultiSeries  LGBMRegressor   
104  ForecasterRecursiveMultiSeries  LGBMRegressor   
116  ForecasterRecursiveMultiSeries  LGBMRegressor   
135  ForecasterRecursiveMultiSeries  LGBMRegressor   
148  ForecasterRecursiveMultiSeries  LGBMRegressor   
161  ForecasterRecursiveMultiSeries  LGBMRegressor   
174  ForecasterRecursiveMultiSeries  LGBMRegressor   
187  ForecasterRecursiveMultiSeries  LGBMRegressor   
201  ForecasterRecursiveMultiSeries  LGBMRegressor   
216  ForecasterRecursiveMultiSeries  LGBMRegressor   
231  ForecasterRecursiveMultiSeries  LGBMRegressor   
246  ForecasterRecursiveMultiSeries  LGBMRegressor   
261  ForecasterRecursiveMultiSeries  LGBMRegressor   
276  ForecasterRecursiveMultiSeries  LGBMRegressor   
291  ForecasterRecursiveMultiSeries  LGBMRegressor   

                                         function_name  \
0    ForecasterRecursiveMultiSeries_fit_series_is_d...   
12   ForecasterRecursiveMultiSeries_fit_series_is_d...   
24   ForecasterRecursiveMultiSeries_fit_series_is_d...   
36   ForecasterRecursiveMultiSeries_fit_series_is_d...   
48   ForecasterRecursiveMultiSeries_fit_series_is_d...   
68   ForecasterRecursiveMultiSeries_fit_series_is_d...   
80   ForecasterRecursiveMultiSeries_fit_series_is_d...   
92   ForecasterRecursiveMultiSeries_fit_series_is_d...   
104  ForecasterRecursiveMultiSeries_fit_series_is_d...   
116  ForecasterRecursiveMultiSeries_fit_series_is_d...   
135  ForecasterRecursiveMultiSeries_fit_series_is_d...   
148  ForecasterRecursiveMultiSeries_fit_series_is_d...   
161  ForecasterRecursiveMultiSeries_fit_series_is_d...   
174  ForecasterRecursiveMultiSeries_fit_series_is_d...   
187  ForecasterRecursiveMultiSeries_fit_series_is_d...   
201  ForecasterRecursiveMultiSeries_fit_series_is_d...   
216  ForecasterRecursiveMultiSeries_fit_series_is_d...   
231  ForecasterRecursiveMultiSeries_fit_series_is_d...   
246  ForecasterRecursiveMultiSeries_fit_series_is_d...   
261  ForecasterRecursiveMultiSeries_fit_series_is_d...   
276  ForecasterRecursiveMultiSeries_fit_series_is_d...   
291  ForecasterRecursiveMultiSeries_fit_series_is_d...   

                        function_hash  run_time_avg  run_time_std_dev  \
0    63b606a379874ae9f340ba4fe592d695     12.293677          0.429946   
12   63b606a379874ae9f340ba4fe592d695     12.290554          0.785076   
24   63b606a379874ae9f340ba4fe592d695     11.181269          0.577565   
36   63b606a379874ae9f340ba4fe592d695     12.332075          1.001781   
48   63b606a379874ae9f340ba4fe592d695     12.542493          0.606813   
68   63b606a379874ae9f340ba4fe592d695     10.987336          0.396632   
80   63b606a379874ae9f340ba4fe592d695     11.761212          0.358871   
92   63b606a379874ae9f340ba4fe592d695     11.800770          0.402881   
104  63b606a379874ae9f340ba4fe592d695     11.717140          0.238003   
116  63b606a379874ae9f340ba4fe592d695     11.314107          0.397571   
135  63b606a379874ae9f340ba4fe592d695     13.482403          1.086462   
148  63b606a379874ae9f340ba4fe592d695     12.650917          1.080875   
161  63b606a379874ae9f340ba4fe592d695     12.449832          0.639767   
174  63b606a379874ae9f340ba4fe592d695     13.398143          0.542395   
187  63b606a379874ae9f340ba4fe592d695     11.392517          0.294351   
201  63b606a379874ae9f340ba4fe592d695     12.833762          0.516694   
216  63b606a379874ae9f340ba4fe592d695      7.599014          0.210753   
231  63b606a379874ae9f340ba4fe592d695      8.396984          0.407490   
246  63b606a379874ae9f340ba4fe592d695      8.086642    

forecaster_name regressor_name  \
1    ForecasterRecursiveMultiSeries  LGBMRegressor   
13   ForecasterRecursiveMultiSeries  LGBMRegressor   
25   ForecasterRecursiveMultiSeries  LGBMRegressor   
37     ForecasterAutoregMultiSeries  LGBMRegressor   
49     ForecasterAutoregMultiSeries  LGBMRegressor   
69   ForecasterRecursiveMultiSeries  LGBMRegressor   
81   ForecasterRecursiveMultiSeries  LGBMRegressor   
93   ForecasterRecursiveMultiSeries  LGBMRegressor   
105  ForecasterRecursiveMultiSeries  LGBMRegressor   
117  ForecasterRecursiveMultiSeries  LGBMRegressor   
136  ForecasterRecursiveMultiSeries  LGBMRegressor   
149  ForecasterRecursiveMultiSeries  LGBMRegressor   
162  ForecasterRecursiveMultiSeries  LGBMRegressor   
175  ForecasterRecursiveMultiSeries  LGBMRegressor   
188  ForecasterRecursiveMultiSeries  LGBMRegressor   
202  ForecasterRecursiveMultiSeries  LGBMRegressor   
217  ForecasterRecursiveMultiSeries  LGBMRegressor   
232  ForecasterRecursiveMultiSeries  LGBMRegressor   
247  ForecasterRecursiveMultiSeries  LGBMRegressor   
262  ForecasterRecursiveMultiSeries  LGBMRegressor   
277  ForecasterRecursiveMultiSeries  LGBMRegressor   
292  ForecasterRecursiveMultiSeries  LGBMRegressor   

                                         function_name  \
1    ForecasterRecursiveMultiSeries__create_train_X...   
13   ForecasterRecursiveMultiSeries__create_train_X...   
25   ForecasterRecursiveMultiSeries__create_train_X...   
37   ForecasterRecursiveMultiSeries__create_train_X...   
49   ForecasterRecursiveMultiSeries__create_train_X...   
69   ForecasterRecursiveMultiSeries__create_train_X...   
81   ForecasterRecursiveMultiSeries__create_train_X...   
93   ForecasterRecursiveMultiSeries__create_train_X...   
105  ForecasterRecursiveMultiSeries__create_train_X...   
117  ForecasterRecursiveMultiSeries__create_train_X...   
136  ForecasterRecursiveMultiSeries__create_train_X...   
149  ForecasterRecursiveMultiSeries__create_train_X...   
162  ForecasterRecursiveMultiSeries__create_train_X...   
175  ForecasterRecursiveMultiSeries__create_train_X...   
188  ForecasterRecursiveMultiSeries__create_train_X...   
202  ForecasterRecursiveMultiSeries__create_train_X...   
217  ForecasterRecursiveMultiSeries__create_train_X...   
232  ForecasterRecursiveMultiSeries__create_train_X...   
247  ForecasterRecursiveMultiSeries__create_train_X...   
262  ForecasterRecursiveMultiSeries__create_train_X...   
277  ForecasterRecursiveMultiSeries__create_train_X...   
292  ForecasterRecursiveMultiSeries__create_train_X...   

                        function_hash  run_time_avg  run_time_std_dev  \
1    583e7d25f58c2314c85ab6c385d879cc      1.594639          0.061033   
13   583e7d25f58c2314c85ab6c385d879cc      1.730657          0.036684   
25   583e7d25f58c2314c85ab6c385d879cc      2.008426          0.020794   
37   583e7d25f58c2314c85ab6c385d879cc      2.624174          0.090886   
49   583e7d25f58c2314c85ab6c385d879cc      2.603322          0.046577   
69   583e7d25f58c2314c85ab6c385d879cc      1.998299          0.020942   
81   583e7d25f58c2314c85ab6c385d879cc      1.760219          0.029486   
93   583e7d25f58c2314c85ab6c385d879cc      1.708451          0.049639   
105  583e7d25f58c2314c85ab6c385d879cc      1.560971          0.057417   
117  583e7d25f58c2314c85ab6c385d879cc      1.534163          0.040951   
136  583e7d25f58c2314c85ab6c385d879cc      1.811675          0.131149   
149  583e7d25f58c2314c85ab6c385d879cc      1.778144          0.056622   
162  583e7d25f58c2314c85ab6c385d879cc      1.678415          0.036097   
175  583e7d25f58c2314c85ab6c385d879cc      2.350689          0.146020   
188  583e7d25f58c2314c85ab6c385d879cc      2.006739          0.027937   
202  583e7d25f58c2314c85ab6c385d879cc      1.607951          0.073839   
217  583e7d25f58c2314c85ab6c385d879cc      1.510267          0.037293   
232  583e7d25f58c2314c85ab6c385d879cc      1.956854          0.089286   
247  583e7d25f58c2314c85ab6c385d879cc      2.114042    

forecaster_name regressor_name  \
2    ForecasterRecursiveMultiSeries  LGBMRegressor   
14   ForecasterRecursiveMultiSeries  LGBMRegressor   
26   ForecasterRecursiveMultiSeries  LGBMRegressor   
38     ForecasterAutoregMultiSeries  LGBMRegressor   
50     ForecasterAutoregMultiSeries  LGBMRegressor   
70   ForecasterRecursiveMultiSeries  LGBMRegressor   
82   ForecasterRecursiveMultiSeries  LGBMRegressor   
94   ForecasterRecursiveMultiSeries  LGBMRegressor   
106  ForecasterRecursiveMultiSeries  LGBMRegressor   
118  ForecasterRecursiveMultiSeries  LGBMRegressor   
137  ForecasterRecursiveMultiSeries  LGBMRegressor   
150  ForecasterRecursiveMultiSeries  LGBMRegressor   
163  ForecasterRecursiveMultiSeries  LGBMRegressor   
176  ForecasterRecursiveMultiSeries  LGBMRegressor   
189  ForecasterRecursiveMultiSeries  LGBMRegressor   
203  ForecasterRecursiveMultiSeries  LGBMRegressor   
218  ForecasterRecursiveMultiSeries  LGBMRegressor   
233  ForecasterRecursiveMultiSeries  LGBMRegressor   
248  ForecasterRecursiveMultiSeries  LGBMRegressor   
263  ForecasterRecursiveMultiSeries  LGBMRegressor   
278  ForecasterRecursiveMultiSeries  LGBMRegressor   
293  ForecasterRecursiveMultiSeries  LGBMRegressor   

                                         function_name  \
2    ForecasterRecursiveMultiSeries_fit_series_is_d...   
14   ForecasterRecursiveMultiSeries_fit_series_is_d...   
26   ForecasterRecursiveMultiSeries_fit_series_is_d...   
38   ForecasterRecursiveMultiSeries_fit_series_is_d...   
50   ForecasterRecursiveMultiSeries_fit_series_is_d...   
70   ForecasterRecursiveMultiSeries_fit_series_is_d...   
82   ForecasterRecursiveMultiSeries_fit_series_is_d...   
94   ForecasterRecursiveMultiSeries_fit_series_is_d...   
106  ForecasterRecursiveMultiSeries_fit_series_is_d...   
118  ForecasterRecursiveMultiSeries_fit_series_is_d...   
137  ForecasterRecursiveMultiSeries_fit_series_is_d...   
150  ForecasterRecursiveMultiSeries_fit_series_is_d...   
163  ForecasterRecursiveMultiSeries_fit_series_is_d...   
176  ForecasterRecursiveMultiSeries_fit_series_is_d...   
189  ForecasterRecursiveMultiSeries_fit_series_is_d...   
203  ForecasterRecursiveMultiSeries_fit_series_is_d...   
218  ForecasterRecursiveMultiSeries_fit_series_is_d...   
233  ForecasterRecursiveMultiSeries_fit_series_is_d...   
248  ForecasterRecursiveMultiSeries_fit_series_is_d...   
263  ForecasterRecursiveMultiSeries_fit_series_is_d...   
278  ForecasterRecursiveMultiSeries_fit_series_is_d...   
293  ForecasterRecursiveMultiSeries_fit_series_is_d...   

                        function_hash  run_time_avg  run_time_std_dev  \
2    aa35b8ba0c0839021a95e5ba0786a67e     11.580742          0.917493   
14   aa35b8ba0c0839021a95e5ba0786a67e     10.828553          0.107749   
26   aa35b8ba0c0839021a95e5ba0786a67e     10.099889          0.160311   
38   aa35b8ba0c0839021a95e5ba0786a67e     11.003430          0.223845   
50   aa35b8ba0c0839021a95e5ba0786a67e     11.890319          0.521044   
70   aa35b8ba0c0839021a95e5ba0786a67e     10.926485          0.812523   
82   aa35b8ba0c0839021a95e5ba0786a67e     11.199184          0.096970   
94   aa35b8ba0c0839021a95e5ba0786a67e     11.031137          0.134091   
106  aa35b8ba0c0839021a95e5ba0786a67e     11.330288          0.895549   
118  aa35b8ba0c0839021a95e5ba0786a67e     10.856502          0.081189   
137  aa35b8ba0c0839021a95e5ba0786a67e     12.595582          0.764868   
150  aa35b8ba0c0839021a95e5ba0786a67e     13.922733          1.839202   
163  aa35b8ba0c0839021a95e5ba0786a67e     12.949121          1.421564   
176  aa35b8ba0c0839021a95e5ba0786a67e     12.067933          0.734881   
189  aa35b8ba0c0839021a95e5ba0786a67e     10.102644          0.154465   
203  aa35b8ba0c0839021a95e5ba0786a67e     11.636991          0.093879   
218  aa35b8ba0c0839021a95e5ba0786a67e      7.479344          0.242101   
233  aa35b8ba0c0839021a95e5ba0786a67e      8.617346          0.276325   
248  aa35b8ba0c0839021a95e5ba0786a67e      6.477069    

forecaster_name regressor_name  \
3    ForecasterRecursiveMultiSeries  LGBMRegressor   
15   ForecasterRecursiveMultiSeries  LGBMRegressor   
27   ForecasterRecursiveMultiSeries  LGBMRegressor   
39     ForecasterAutoregMultiSeries  LGBMRegressor   
51     ForecasterAutoregMultiSeries  LGBMRegressor   
71   ForecasterRecursiveMultiSeries  LGBMRegressor   
83   ForecasterRecursiveMultiSeries  LGBMRegressor   
95   ForecasterRecursiveMultiSeries  LGBMRegressor   
107  ForecasterRecursiveMultiSeries  LGBMRegressor   
119  ForecasterRecursiveMultiSeries  LGBMRegressor   
138  ForecasterRecursiveMultiSeries  LGBMRegressor   
151  ForecasterRecursiveMultiSeries  LGBMRegressor   
164  ForecasterRecursiveMultiSeries  LGBMRegressor   
177  ForecasterRecursiveMultiSeries  LGBMRegressor   
190  ForecasterRecursiveMultiSeries  LGBMRegressor   
204  ForecasterRecursiveMultiSeries  LGBMRegressor   
219  ForecasterRecursiveMultiSeries  LGBMRegressor   
234  ForecasterRecursiveMultiSeries  LGBMRegressor   
249  ForecasterRecursiveMultiSeries  LGBMRegressor   
264  ForecasterRecursiveMultiSeries  LGBMRegressor   
279  ForecasterRecursiveMultiSeries  LGBMRegressor   
294  ForecasterRecursiveMultiSeries  LGBMRegressor   

                                         function_name  \
3    ForecasterRecursiveMultiSeries__create_train_X...   
15   ForecasterRecursiveMultiSeries__create_train_X...   
27   ForecasterRecursiveMultiSeries__create_train_X...   
39   ForecasterRecursiveMultiSeries__create_train_X...   
51   ForecasterRecursiveMultiSeries__create_train_X...   
71   ForecasterRecursiveMultiSeries__create_train_X...   
83   ForecasterRecursiveMultiSeries__create_train_X...   
95   ForecasterRecursiveMultiSeries__create_train_X...   
107  ForecasterRecursiveMultiSeries__create_train_X...   
119  ForecasterRecursiveMultiSeries__create_train_X...   
138  ForecasterRecursiveMultiSeries__create_train_X...   
151  ForecasterRecursiveMultiSeries__create_train_X...   
164  ForecasterRecursiveMultiSeries__create_train_X...   
177  ForecasterRecursiveMultiSeries__create_train_X...   
190  ForecasterRecursiveMultiSeries__create_train_X...   
204  ForecasterRecursiveMultiSeries__create_train_X...   
219  ForecasterRecursiveMultiSeries__create_train_X...   
234  ForecasterRecursiveMultiSeries__create_train_X...   
249  ForecasterRecursiveMultiSeries__create_train_X...   
264  ForecasterRecursiveMultiSeries__create_train_X...   
279  ForecasterRecursiveMultiSeries__create_train_X...   
294  ForecasterRecursiveMultiSeries__create_train_X...   

                        function_hash  run_time_avg  run_time_std_dev  \
3    7b994fdfa33ce4a2084e303d3f49c934      1.224587          0.055873   
15   7b994fdfa33ce4a2084e303d3f49c934      1.375285          0.040809   
27   7b994fdfa33ce4a2084e303d3f49c934      1.517815          0.064871   
39   7b994fdfa33ce4a2084e303d3f49c934      2.004793          0.040390   
51   7b994fdfa33ce4a2084e303d3f49c934      2.146876          0.070924   
71   7b994fdfa33ce4a2084e303d3f49c934      1.568071          0.119750   
83   7b994fdfa33ce4a2084e303d3f49c934      1.411051          0.055234   
95   7b994fdfa33ce4a2084e303d3f49c934      1.385172          0.047952   
107  7b994fdfa33ce4a2084e303d3f49c934      1.270865          0.041491   
119  7b994fdfa33ce4a2084e303d3f49c934      1.206709          0.044674   
138  7b994fdfa33ce4a2084e303d3f49c934      1.197850          0.055166   
151  7b994fdfa33ce4a2084e303d3f49c934      1.406918          0.044804   
164  7b994fdfa33ce4a2084e303d3f49c934      1.521542          0.186202   
177  7b994fdfa33ce4a2084e303d3f49c934      1.744641          0.158125   
190  7b994fdfa33ce4a2084e303d3f49c934      1.509208          0.036639   
204  7b994fdfa33ce4a2084e303d3f49c934      1.255405          0.049512   
219  7b994fdfa33ce4a2084e303d3f49c934      1.279314          0.055151   
234  7b994fdfa33ce4a2084e303d3f49c934      1.571599          0.091096   
249  7b994fdfa33ce4a2084e303d3f49c934      1.375553    

forecaster_name regressor_name  \
4    ForecasterRecursiveMultiSeries  LGBMRegressor   
16   ForecasterRecursiveMultiSeries  LGBMRegressor   
28   ForecasterRecursiveMultiSeries  LGBMRegressor   
40     ForecasterAutoregMultiSeries  LGBMRegressor   
52     ForecasterAutoregMultiSeries  LGBMRegressor   
72   ForecasterRecursiveMultiSeries  LGBMRegressor   
84   ForecasterRecursiveMultiSeries  LGBMRegressor   
96   ForecasterRecursiveMultiSeries  LGBMRegressor   
108  ForecasterRecursiveMultiSeries  LGBMRegressor   
120  ForecasterRecursiveMultiSeries  LGBMRegressor   
139  ForecasterRecursiveMultiSeries  LGBMRegressor   
152  ForecasterRecursiveMultiSeries  LGBMRegressor   
165  ForecasterRecursiveMultiSeries  LGBMRegressor   
178  ForecasterRecursiveMultiSeries  LGBMRegressor   
191  ForecasterRecursiveMultiSeries  LGBMRegressor   
205  ForecasterRecursiveMultiSeries  LGBMRegressor   
220  ForecasterRecursiveMultiSeries  LGBMRegressor   
235  ForecasterRecursiveMultiSeries  LGBMRegressor   
250  ForecasterRecursiveMultiSeries  LGBMRegressor   
265  ForecasterRecursiveMultiSeries  LGBMRegressor   
280  ForecasterRecursiveMultiSeries  LGBMRegressor   
295  ForecasterRecursiveMultiSeries  LGBMRegressor   

                                         function_name  \
4    ForecasterRecursiveMultiSeries__create_train_X...   
16   ForecasterRecursiveMultiSeries__create_train_X...   
28   ForecasterRecursiveMultiSeries__create_train_X...   
40   ForecasterRecursiveMultiSeries__create_train_X...   
52   ForecasterRecursiveMultiSeries__create_train_X...   
72   ForecasterRecursiveMultiSeries__create_train_X...   
84   ForecasterRecursiveMultiSeries__create_train_X...   
96   ForecasterRecursiveMultiSeries__create_train_X...   
108  ForecasterRecursiveMultiSeries__create_train_X...   
120  ForecasterRecursiveMultiSeries__create_train_X...   
139  ForecasterRecursiveMultiSeries__create_train_X...   
152  ForecasterRecursiveMultiSeries__create_train_X...   
165  ForecasterRecursiveMultiSeries__create_train_X...   
178  ForecasterRecursiveMultiSeries__create_train_X...   
191  ForecasterRecursiveMultiSeries__create_train_X...   
205  ForecasterRecursiveMultiSeries__create_train_X...   
220  ForecasterRecursiveMultiSeries__create_train_X...   
235  ForecasterRecursiveMultiSeries__create_train_X...   
250  ForecasterRecursiveMultiSeries__create_train_X...   
265  ForecasterRecursiveMultiSeries__create_train_X...   
280  ForecasterRecursiveMultiSeries__create_train_X...   
295  ForecasterRecursiveMultiSeries__create_train_X...   

                        function_hash  run_time_avg  run_time_std_dev  \
4    ea2ceb1c912245376ba4cea7595175be      0.001306          0.000172   
16   ea2ceb1c912245376ba4cea7595175be      0.001370          0.000224   
28   ea2ceb1c912245376ba4cea7595175be      0.001605          0.000359   
40   ea2ceb1c912245376ba4cea7595175be      0.001624          0.000139   
52   ea2ceb1c912245376ba4cea7595175be      0.002253          0.000301   
72   ea2ceb1c912245376ba4cea7595175be      0.003732          0.000383   
84   ea2ceb1c912245376ba4cea7595175be      0.001514          0.000252   
96   ea2ceb1c912245376ba4cea7595175be      0.001539          0.000270   
108  ea2ceb1c912245376ba4cea7595175be      0.001319          0.000149   
120  ea2ceb1c912245376ba4cea7595175be      0.001437          0.000155   
139  ea2ceb1c912245376ba4cea7595175be      0.001451          0.000119   
152  ea2ceb1c912245376ba4cea7595175be      0.001269          0.000178   
165  ea2ceb1c912245376ba4cea7595175be      0.001208          0.000087   
178  ea2ceb1c912245376ba4cea7595175be      0.001409          0.000156   
191  ea2ceb1c912245376ba4cea7595175be      0.001398          0.000155   
205  ea2ceb1c912245376ba4cea7595175be      0.001546          0.000192   
220  ea2ceb1c912245376ba4cea7595175be      0.001447          0.000320   
235  ea2ceb1c912245376ba4cea7595175be      0.001386          0.000332   
250  ea2ceb1c912245376ba4cea7595175be      0.000964    

forecaster_name regressor_name  \
5    ForecasterRecursiveMultiSeries  LGBMRegressor   
17   ForecasterRecursiveMultiSeries  LGBMRegressor   
29   ForecasterRecursiveMultiSeries  LGBMRegressor   
41     ForecasterAutoregMultiSeries  LGBMRegressor   
53     ForecasterAutoregMultiSeries  LGBMRegressor   
73   ForecasterRecursiveMultiSeries  LGBMRegressor   
85   ForecasterRecursiveMultiSeries  LGBMRegressor   
97   ForecasterRecursiveMultiSeries  LGBMRegressor   
109  ForecasterRecursiveMultiSeries  LGBMRegressor   
121  ForecasterRecursiveMultiSeries  LGBMRegressor   
140  ForecasterRecursiveMultiSeries  LGBMRegressor   
153  ForecasterRecursiveMultiSeries  LGBMRegressor   
166  ForecasterRecursiveMultiSeries  LGBMRegressor   
179  ForecasterRecursiveMultiSeries  LGBMRegressor   
192  ForecasterRecursiveMultiSeries  LGBMRegressor   
206  ForecasterRecursiveMultiSeries  LGBMRegressor   
221  ForecasterRecursiveMultiSeries  LGBMRegressor   
236  ForecasterRecursiveMultiSeries  LGBMRegressor   
251  ForecasterRecursiveMultiSeries  LGBMRegressor   
266  ForecasterRecursiveMultiSeries  LGBMRegressor   
281  ForecasterRecursiveMultiSeries  LGBMRegressor   
296  ForecasterRecursiveMultiSeries  LGBMRegressor   

                                         function_name  \
5    ForecasterRecursiveMultiSeries_predict_exog_is...   
17   ForecasterRecursiveMultiSeries_predict_exog_is...   
29   ForecasterRecursiveMultiSeries_predict_exog_is...   
41   ForecasterRecursiveMultiSeries_predict_exog_is...   
53   ForecasterRecursiveMultiSeries_predict_exog_is...   
73   ForecasterRecursiveMultiSeries_predict_exog_is...   
85   ForecasterRecursiveMultiSeries_predict_exog_is...   
97   ForecasterRecursiveMultiSeries_predict_exog_is...   
109  ForecasterRecursiveMultiSeries_predict_exog_is...   
121  ForecasterRecursiveMultiSeries_predict_exog_is...   
140  ForecasterRecursiveMultiSeries_predict_exog_is...   
153  ForecasterRecursiveMultiSeries_predict_exog_is...   
166  ForecasterRecursiveMultiSeries_predict_exog_is...   
179  ForecasterRecursiveMultiSeries_predict_exog_is...   
192  ForecasterRecursiveMultiSeries_predict_exog_is...   
206  ForecasterRecursiveMultiSeries_predict_exog_is...   
221  ForecasterRecursiveMultiSeries_predict_exog_is...   
236  ForecasterRecursiveMultiSeries_predict_exog_is...   
251  ForecasterRecursiveMultiSeries_predict_exog_is...   
266  ForecasterRecursiveMultiSeries_predict_exog_is...   
281  ForecasterRecursiveMultiSeries_predict_exog_is...   
296  ForecasterRecursiveMultiSeries_predict_exog_is...   

                        function_hash  run_time_avg  run_time_std_dev  \
5    451898dccb92cc6f0a674d62eb66e4d8      0.451472          0.038231   
17   451898dccb92cc6f0a674d62eb66e4d8      1.681694          0.031587   
29   451898dccb92cc6f0a674d62eb66e4d8      1.632832          0.007875   
41   451898dccb92cc6f0a674d62eb66e4d8     42.354621          1.205520   
53   451898dccb92cc6f0a674d62eb66e4d8     43.534917          2.283648   
73   451898dccb92cc6f0a674d62eb66e4d8      1.796171          0.151445   
85   451898dccb92cc6f0a674d62eb66e4d8      1.703143          0.009877   
97   451898dccb92cc6f0a674d62eb66e4d8      1.695652          0.028556   
109  451898dccb92cc6f0a674d62eb66e4d8      0.463045          0.041767   
121  451898dccb92cc6f0a674d62eb66e4d8      0.461218          0.038811   
140  451898dccb92cc6f0a674d62eb66e4d8      0.445907          0.031986   
153  451898dccb92cc6f0a674d62eb66e4d8      1.701058          0.093446   
166  451898dccb92cc6f0a674d62eb66e4d8      1.698835          0.102595   
179  451898dccb92cc6f0a674d62eb66e4d8      1.764211          0.083903   
192  451898dccb92cc6f0a674d62eb66e4d8      1.675546          0.027637   
206  451898dccb92cc6f0a674d62eb66e4d8      0.492879          0.043107   
221  451898dccb92cc6f0a674d62eb66e4d8      0.414709          0.053413   
236  451898dccb92cc6f0a674d62eb66e4d8      1.355339          0.058051   
251  451898dccb92cc6f0a674d62eb66e4d8      1.133120    

forecaster_name regressor_name  \
6    ForecasterRecursiveMultiSeries  LGBMRegressor   
18   ForecasterRecursiveMultiSeries  LGBMRegressor   
30   ForecasterRecursiveMultiSeries  LGBMRegressor   
42     ForecasterAutoregMultiSeries  LGBMRegressor   
54     ForecasterAutoregMultiSeries  LGBMRegressor   
74   ForecasterRecursiveMultiSeries  LGBMRegressor   
86   ForecasterRecursiveMultiSeries  LGBMRegressor   
98   ForecasterRecursiveMultiSeries  LGBMRegressor   
110  ForecasterRecursiveMultiSeries  LGBMRegressor   
122  ForecasterRecursiveMultiSeries  LGBMRegressor   
141  ForecasterRecursiveMultiSeries  LGBMRegressor   
154  ForecasterRecursiveMultiSeries  LGBMRegressor   
167  ForecasterRecursiveMultiSeries  LGBMRegressor   
180  ForecasterRecursiveMultiSeries  LGBMRegressor   
193  ForecasterRecursiveMultiSeries  LGBMRegressor   
207  ForecasterRecursiveMultiSeries  LGBMRegressor   
222  ForecasterRecursiveMultiSeries  LGBMRegressor   
237  ForecasterRecursiveMultiSeries  LGBMRegressor   
252  ForecasterRecursiveMultiSeries  LGBMRegressor   
267  ForecasterRecursiveMultiSeries  LGBMRegressor   
282  ForecasterRecursiveMultiSeries  LGBMRegressor   
297  ForecasterRecursiveMultiSeries  LGBMRegressor   

                                         function_name  \
6    ForecasterRecursiveMultiSeries__create_predict...   
18   ForecasterRecursiveMultiSeries__create_predict...   
30   ForecasterRecursiveMultiSeries__create_predict...   
42   ForecasterRecursiveMultiSeries__create_predict...   
54   ForecasterRecursiveMultiSeries__create_predict...   
74   ForecasterRecursiveMultiSeries__create_predict...   
86   ForecasterRecursiveMultiSeries__create_predict...   
98   ForecasterRecursiveMultiSeries__create_predict...   
110  ForecasterRecursiveMultiSeries__create_predict...   
122  ForecasterRecursiveMultiSeries__create_predict...   
141  ForecasterRecursiveMultiSeries__create_predict...   
154  ForecasterRecursiveMultiSeries__create_predict...   
167  ForecasterRecursiveMultiSeries__create_predict...   
180  ForecasterRecursiveMultiSeries__create_predict...   
193  ForecasterRecursiveMultiSeries__create_predict...   
207  ForecasterRecursiveMultiSeries__create_predict...   
222  ForecasterRecursiveMultiSeries__create_predict...   
237  ForecasterRecursiveMultiSeries__create_predict...   
252  ForecasterRecursiveMultiSeries__create_predict...   
267  ForecasterRecursiveMultiSeries__create_predict...   
282  ForecasterRecursiveMultiSeries__create_predict...   
297  ForecasterRecursiveMultiSeries__create_predict...   

                        function_hash  run_time_avg  run_time_std_dev  \
6    52b1c12811cade5921c24c58d5503d03      0.294342          0.032782   
18   52b1c12811cade5921c24c58d5503d03      1.551544          0.048945   
30   52b1c12811cade5921c24c58d5503d03      1.508526          0.016043   
42   52b1c12811cade5921c24c58d5503d03           NaN               NaN   
54   52b1c12811cade5921c24c58d5503d03           NaN               NaN   
74   52b1c12811cade5921c24c58d5503d03      1.582764          0.096881   
86   52b1c12811cade5921c24c58d5503d03      1.705099          0.281979   
98   52b1c12811cade5921c24c58d5503d03      1.547401          0.029990   
110  52b1c12811cade5921c24c58d5503d03      0.300234          0.034957   
122  52b1c12811cade5921c24c58d5503d03      0.306396          0.038716   
141  52b1c12811cade5921c24c58d5503d03      0.294692          0.034340   
154  52b1c12811cade5921c24c58d5503d03      1.447513          0.027566   
167  52b1c12811cade5921c24c58d5503d03      1.663521          0.113653   
180  52b1c12811cade5921c24c58d5503d03      1.693156          0.159579   
193  52b1c12811cade5921c24c58d5503d03      1.547912          0.035664   
207  52b1c12811cade5921c24c58d5503d03      0.306145          0.035830   
222  52b1c12811cade5921c24c58d5503d03      0.270943          0.048715   
237  52b1c12811cade5921c24c58d5503d03      1.205738          0.070470   
252  52b1c12811cade5921c24c58d5503d03      1.003418    

forecaster_name regressor_name  \
7    ForecasterRecursiveMultiSeries  LGBMRegressor   
19   ForecasterRecursiveMultiSeries  LGBMRegressor   
31   ForecasterRecursiveMultiSeries  LGBMRegressor   
43     ForecasterAutoregMultiSeries  LGBMRegressor   
55     ForecasterAutoregMultiSeries  LGBMRegressor   
75   ForecasterRecursiveMultiSeries  LGBMRegressor   
87   ForecasterRecursiveMultiSeries  LGBMRegressor   
99   ForecasterRecursiveMultiSeries  LGBMRegressor   
111  ForecasterRecursiveMultiSeries  LGBMRegressor   
123  ForecasterRecursiveMultiSeries  LGBMRegressor   
142  ForecasterRecursiveMultiSeries  LGBMRegressor   
155  ForecasterRecursiveMultiSeries  LGBMRegressor   
168  ForecasterRecursiveMultiSeries  LGBMRegressor   
181  ForecasterRecursiveMultiSeries  LGBMRegressor   
194  ForecasterRecursiveMultiSeries  LGBMRegressor   
208  ForecasterRecursiveMultiSeries  LGBMRegressor   
223  ForecasterRecursiveMultiSeries  LGBMRegressor   
238  ForecasterRecursiveMultiSeries  LGBMRegressor   
253  ForecasterRecursiveMultiSeries  LGBMRegressor   
268  ForecasterRecursiveMultiSeries  LGBMRegressor   
283  ForecasterRecursiveMultiSeries  LGBMRegressor   
298  ForecasterRecursiveMultiSeries  LGBMRegressor   

                                         function_name  \
7    ForecasterRecursiveMultiSeries__check_predict_...   
19   ForecasterRecursiveMultiSeries__check_predict_...   
31   ForecasterRecursiveMultiSeries__check_predict_...   
43   ForecasterRecursiveMultiSeries__check_predict_...   
55   ForecasterRecursiveMultiSeries__check_predict_...   
75   ForecasterRecursiveMultiSeries__check_predict_...   
87   ForecasterRecursiveMultiSeries__check_predict_...   
99   ForecasterRecursiveMultiSeries__check_predict_...   
111  ForecasterRecursiveMultiSeries__check_predict_...   
123  ForecasterRecursiveMultiSeries__check_predict_...   
142  ForecasterRecursiveMultiSeries__check_predict_...   
155  ForecasterRecursiveMultiSeries__check_predict_...   
168  ForecasterRecursiveMultiSeries__check_predict_...   
181  ForecasterRecursiveMultiSeries__check_predict_...   
194  ForecasterRecursiveMultiSeries__check_predict_...   
208  ForecasterRecursiveMultiSeries__check_predict_...   
223  ForecasterRecursiveMultiSeries__check_predict_...   
238  ForecasterRecursiveMultiSeries__check_predict_...   
253  ForecasterRecursiveMultiSeries__check_predict_...   
268  ForecasterRecursiveMultiSeries__check_predict_...   
283  ForecasterRecursiveMultiSeries__check_predict_...   
298  ForecasterRecursiveMultiSeries__check_predict_...   

                        function_hash  run_time_avg  run_time_std_dev  \
7    33fe67969d33981cb73558c1dc51eb82      0.075259          0.011461   
19   33fe67969d33981cb73558c1dc51eb82      0.285421          0.006976   
31   33fe67969d33981cb73558c1dc51eb82      0.292057          0.017751   
43   33fe67969d33981cb73558c1dc51eb82           NaN               NaN   
55   33fe67969d33981cb73558c1dc51eb82           NaN               NaN   
75   33fe67969d33981cb73558c1dc51eb82      0.320222          0.009129   
87   33fe67969d33981cb73558c1dc51eb82      0.422475          0.069229   
99   33fe67969d33981cb73558c1dc51eb82      0.288091          0.006007   
111  33fe67969d33981cb73558c1dc51eb82      0.068207          0.000755   
123  33fe67969d33981cb73558c1dc51eb82      0.078871          0.014604   
142  33fe67969d33981cb73558c1dc51eb82      0.068249          0.000627   
155  33fe67969d33981cb73558c1dc51eb82      0.274099          0.011273   
168  33fe67969d33981cb73558c1dc51eb82      0.362666          0.050402   
181  33fe67969d33981cb73558c1dc51eb82      0.338939          0.046904   
194  33fe67969d33981cb73558c1dc51eb82      0.291854          0.011241   
208  33fe67969d33981cb73558c1dc51eb82      0.072865          0.002260   
223  33fe67969d33981cb73558c1dc51eb82      0.065062          0.012139   
238  33fe67969d33981cb73558c1dc51eb82      0.200559          0.012927   
253  33fe67969d33981cb73558c1dc51eb82      0.178378    

forecaster_name regressor_name  \
128  ForecasterRecursiveMultiSeries  LGBMRegressor   
133  ForecasterRecursiveMultiSeries  LGBMRegressor   
134  ForecasterRecursiveMultiSeries  LGBMRegressor   
143  ForecasterRecursiveMultiSeries  LGBMRegressor   
156  ForecasterRecursiveMultiSeries  LGBMRegressor   
169  ForecasterRecursiveMultiSeries  LGBMRegressor   
182  ForecasterRecursiveMultiSeries  LGBMRegressor   
195  ForecasterRecursiveMultiSeries  LGBMRegressor   
209  ForecasterRecursiveMultiSeries  LGBMRegressor   
224  ForecasterRecursiveMultiSeries  LGBMRegressor   
239  ForecasterRecursiveMultiSeries  LGBMRegressor   
254  ForecasterRecursiveMultiSeries  LGBMRegressor   
269  ForecasterRecursiveMultiSeries  LGBMRegressor   
284  ForecasterRecursiveMultiSeries  LGBMRegressor   
299  ForecasterRecursiveMultiSeries  LGBMRegressor   

                                         function_name  \
128  ForecasterRecursiveMultiSeries_backtesting_ser...   
133  ForecasterRecursiveMultiSeries_backtesting_ser...   
134  ForecasterRecursiveMultiSeries_backtesting_ser...   
143  ForecasterRecursiveMultiSeries_backtesting_ser...   
156  ForecasterRecursiveMultiSeries_backtesting_ser...   
169  ForecasterRecursiveMultiSeries_backtesting_ser...   
182  ForecasterRecursiveMultiSeries_backtesting_ser...   
195  ForecasterRecursiveMultiSeries_backtesting_ser...   
209  ForecasterRecursiveMultiSeries_backtesting_ser...   
224  ForecasterRecursiveMultiSeries_backtesting_ser...   
239  ForecasterRecursiveMultiSeries_backtesting_ser...   
254  ForecasterRecursiveMultiSeries_backtesting_ser...   
269  ForecasterRecursiveMultiSeries_backtesting_ser...   
284  ForecasterRecursiveMultiSeries_backtesting_ser...   
299  ForecasterRecursiveMultiSeries_backtesting_ser...   

                        function_hash  run_time_avg  run_time_std_dev  \
128  81259b5066e4c039ab1805445e26e639           NaN               NaN   
133  045a2922d13f7327fc5635f0fa1d968e           NaN               NaN   
134  5c9a4d89a695fe2ded0327ec81495237     19.799778          1.440243   
143  21928d6bc9058a601b52a861e58a4cfb     22.981285          1.349951   
156  21928d6bc9058a601b52a861e58a4cfb     38.222740          0.253136   
169  21928d6bc9058a601b52a861e58a4cfb     43.853923          3.686905   
182  21928d6bc9058a601b52a861e58a4cfb     42.174608          1.797158   
195  764622d682985b184e7b2369791c61a1     41.622226          2.192564   
209  764622d682985b184e7b2369791c61a1     21.979430          0.147381   
224  764622d682985b184e7b2369791c61a1     17.687704          0.255780   
239  764622d682985b184e7b2369791c61a1     33.896880          0.406957   
254  764622d682985b184e7b2369791c61a1     26.872867          0.148170   
269  764622d682985b184e7b2369791c61a1     27.242620          0.202290   
284  764622d682985b184e7b2369791c61a1     33.854358          0.383979   
299  764622d682985b184e7b2369791c61a1     18.261195          0.347515   

                      datetime python_version skforecast_version  \
128 2025-04-23 20:07:35.146022         3.12.9             0.16.0   
133 2025-04-23 20:08:07.633611         3.12.9             0.16.0   
134 2025-04-23 20:08:27.626583         3.12.9             0.16.0   
143 2025-04-23 20:13:13.189265         3.12.9             0.16.0   
156 2025-04-23 20:19:24.990623         3.12.9             0.15.1   
169 2025-04-23 22:00:26.938013         3.12.9             0.15.1   
182 2025-04-23 22:13:33.028822         3.12.9             0.14.0   
195 2025-04-23 22:47:46.896636         3.12.9             0.14.0   
209 2025-04-23 22:56:07.201614         3.12.9             0.16.0   
224 2025-04-24 10:29:37.342522        3.11.10             0.16.0   
239 2025-04-24 10:37:42.452354        3.11.10             0.15.1   
254 2025-04-24 10:43:59.665535        3.11.10             0.14.0   
269 2025-04-24 11:11:15.199890        3.11.10             0.14.0   
284 2025-04-24 11:21:01.508197        3.11.10             0.15.1   
299 2025-04-24 11:34:14.472645       

forecaster_name regressor_name  \
210  ForecasterRecursiveMultiSeries  LGBMRegressor   
225  ForecasterRecursiveMultiSeries  LGBMRegressor   
240  ForecasterRecursiveMultiSeries  LGBMRegressor   
255  ForecasterRecursiveMultiSeries  LGBMRegressor   
270  ForecasterRecursiveMultiSeries  LGBMRegressor   
285  ForecasterRecursiveMultiSeries  LGBMRegressor   
300  ForecasterRecursiveMultiSeries  LGBMRegressor   

                                         function_name  \
210  ForecasterRecursiveMultiSeries_backtesting_ser...   
225  ForecasterRecursiveMultiSeries_backtesting_ser...   
240  ForecasterRecursiveMultiSeries_backtesting_ser...   
255  ForecasterRecursiveMultiSeries_backtesting_ser...   
270  ForecasterRecursiveMultiSeries_backtesting_ser...   
285  ForecasterRecursiveMultiSeries_backtesting_ser...   
300  ForecasterRecursiveMultiSeries_backtesting_ser...   

                        function_hash  run_time_avg  run_time_std_dev  \
210  77968c38bfc431991b56a6500970e471     14.999100          0.478435   
225  77968c38bfc431991b56a6500970e471     11.166385          0.685542   
240  77968c38bfc431991b56a6500970e471     12.627921          0.484849   
255  77968c38bfc431991b56a6500970e471     10.287719          0.213035   
270  77968c38bfc431991b56a6500970e471     10.403703          0.137579   
285  77968c38bfc431991b56a6500970e471     12.782420          0.155627   
300  77968c38bfc431991b56a6500970e471     12.247878          0.891811   

                      datetime python_version skforecast_version  \
210 2025-04-23 22:57:57.105248         3.12.9             0.16.0   
225 2025-04-24 10:30:33.198085        3.11.10             0.16.0   
240 2025-04-24 10:38:45.612438        3.11.10             0.15.1   
255 2025-04-24 10:44:51.118971        3.11.10             0.14.0   
270 2025-04-24 11:12:07.236935        3.11.10             0.14.0   
285 2025-04-24 11:22:05.448858        3.11.10             0.15.1   
300 2025-04-24 11:35:15.728040        3.11.10             0.16.0   

    numpy_version pandas_version sklearn_version lightgbm_version  \
210         2.2.5          2.2.3           1.6.1            4.6.0   
225         2.1.3          2.2.3           1.6.1            4.5.0   
240         2.1.3          2.2.3           1.6.1            4.5.0   
255         2.1.3          2.2.3           1.6.1            4.5.0   
270         2.1.3          2.2.3           1.6.1            4.5.0   
285         2.1.3          2.2.3           1.6.1            4.5.0   
300         2.1.3          2.2.3           1.6.1            4.5.0   

                                          platform  \
210  Linux-6.11.0-21-generic-x86_64-with-glibc2.39   
225                      Windows-10-10.0.19045-SP0   
240                      Windows-10-10.0.19045-SP0   
255                      Windows-10-10.0.19045-SP0   
270                      Windows-10-10.0.19045-SP0   
285                      Windows-10-10.0.19045-SP0   
300                      Windows-10-10.0.19045-SP0   

                                             processor  cpu_count  memory_gb  
210                                             x86_64          8      16.64  
225  Intel64 Family 6 Model 141 Stepping 1, Genuine...         16      34.07  
240  Intel64 Family 6 Model 141 Stepping 1, Genuine...         16      34.07  
255  Intel64 Family 6 Model 141 Stepping 1, Genuine...         16      34.07  
270  Intel64 Family 6 Model 141 Stepping 1, Genuine...         16      34.07  
285  Intel64 Family 6 Model 141 Stepping 1, Genuine...         16      34.07  
300  Intel64 Family 6 Model 141 Stepping 1, Genuine...         16      34.07

# ForecasterRecursive

In [10]:
# Mock data for benchmarking
# ==========================================================
len_series = 2000
rng = np.random.default_rng(321)
y = pd.Series(
        data = rng.normal(loc=20, scale=5, size=len_series),
        index=pd.date_range(
            start='2010-01-01',
            periods=len_series,
            freq='h'
        ),
        name='y'
    )
rng = np.random.default_rng(321)
exog = pd.DataFrame(index=y.index)
exog['day_of_week'] = exog.index.dayofweek
exog['week_of_year'] = exog.index.isocalendar().week.astype(int)
exog['month'] = exog.index.month
exog_prediction = pd.DataFrame(
                    index=pd.date_range(
                        start=series_dict[k].index.max() + pd.Timedelta(hours=1),
                        periods=100,
                        freq='h'
                    )
                 ) 
exog_prediction['day_of_week'] = exog_prediction.index.dayofweek
exog_prediction['week_of_year'] = exog_prediction.index.isocalendar().week.astype(int)
exog_prediction['month'] = exog_prediction.index.month

In [11]:
# Benchmarking speed ForecasterRecursive
# ==============================================================================
regressor = LGBMRegressor(random_state=8520, verbose=-1)
if skforecast.__version__ >= '0.14.0':
    forecaster = ForecasterRecursive(
        regressor=regressor,
        lags=50,
        transformer_y=StandardScaler(),
        transformer_exog=StandardScaler(),
    )
else:
    forecaster = ForecasterAutoreg(
        regressor=regressor,
        lags=50,
        transformer_y=StandardScaler(),
        transformer_exog=StandardScaler(),
    )

def ForecasterRecursive_fit():
    forecaster.fit(y=y, exog=exog)

def ForecasterRecursive__create_train_X_y():
    if skforecast.__version__ >= '0.14.0':
        forecaster._create_train_X_y(y=y, exog=exog)
    else:
        forecaster.create_train_X_y(y=y, exog=exog)


def ForecasterRecursive_predict():
    forecaster.predict(steps=100, exog=exog_prediction)

def ForecasterRecursive__create_predict_inputs():
    _ = forecaster._create_predict_inputs(
            steps        = 100,
            exog         = exog_prediction,
            check_inputs = True
        )
    
def ForecasterRecursive_backtesting():
    if skforecast.__version__ >= '0.14.0':
        cv = TimeSeriesFold(
                initial_train_size=1200,
                fixed_train_size=True,
                steps=50,
            )
        _ = backtesting_forecaster(
                forecaster=forecaster,
                y=y,
                exog=exog,
                cv=cv,
                metric='mean_squared_error',
                show_progress=False
            )
    else:
        _ = backtesting_forecaster(
                forecaster=forecaster,
                y=y,
                exog=exog,
                initial_train_size=1200,
                fixed_train_size=True,
                steps=50,
                metric='mean_squared_error',
                show_progress=False
            )


runner = BenchmarkRunner(repeat=30, output_dir="./")
_ = runner.benchmark(ForecasterRecursive__create_train_X_y, forecaster=forecaster)

runner = BenchmarkRunner(repeat=10, output_dir="./")
_ = runner.benchmark(ForecasterRecursive_fit, forecaster=forecaster)

runner = BenchmarkRunner(repeat=30, output_dir="./")
forecaster.fit(y=y, exog=exog)
_ = runner.benchmark(ForecasterRecursive_predict, forecaster=forecaster)
_ = runner.benchmark(ForecasterRecursive__create_predict_inputs, forecaster=forecaster)

runner = BenchmarkRunner(repeat=5, output_dir="./")
_ = runner.benchmark(ForecasterRecursive_backtesting, forecaster=forecaster)

Benchmarking function: ForecasterRecursive__create_train_X_y with skforecast version 0.16.0
Benchmarking function: ForecasterRecursive_fit with skforecast version 0.16.0


c:\Users\jaesc2\Miniconda3\envs\skforecast_py11_2\Lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning:

'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.

c:\Users\jaesc2\Miniconda3\envs\skforecast_py11_2\Lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning:

'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.

c:\Users\jaesc2\Miniconda3\envs\skforecast_py11_2\Lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning:

'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.

c:\Users\jaesc2\Miniconda3\envs\skforecast_py11_2\Lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning:

'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.

c:\Users\jaesc2\Miniconda3\envs\skforecast_py11_2\Lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning:

'force_all_finite' was renamed to 'ensure_all_fini

Benchmarking function: ForecasterRecursive_predict with skforecast version 0.16.0
Benchmarking function: ForecasterRecursive__create_predict_inputs with skforecast version 0.16.0


c:\Users\jaesc2\Miniconda3\envs\skforecast_py11_2\Lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning:

'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.

c:\Users\jaesc2\Miniconda3\envs\skforecast_py11_2\Lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning:

'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.

c:\Users\jaesc2\Miniconda3\envs\skforecast_py11_2\Lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning:

'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.

c:\Users\jaesc2\Miniconda3\envs\skforecast_py11_2\Lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning:

'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.

c:\Users\jaesc2\Miniconda3\envs\skforecast_py11_2\Lib\site-packages\sklearn\utils\deprecation.py:151: FutureWarning:

'force_all_finite' was renamed to 'ensure_all_fini

Benchmarking function: ForecasterRecursive_backtesting with skforecast version 0.16.0


In [12]:
# Plot results
# ==============================================================================
results_benchmark_all = joblib.load("./benchmark.joblib")
results_benchmark = results_benchmark_all.query("forecaster_name in ['ForecasterRecursive', 'ForecasterAutoreg']").copy()
results_benchmark = results_benchmark.query("regressor_name == 'LGBMRegressor'").copy()
for function_name in results_benchmark['function_name'].unique():
    df = results_benchmark.query(f"function_name == '{function_name}'").copy()
    display(df)
    plot_benchmark_results(df, function_name)

forecaster_name regressor_name            function_name  \
8    ForecasterRecursive  LGBMRegressor  ForecasterRecursive_fit   
20   ForecasterRecursive  LGBMRegressor  ForecasterRecursive_fit   
32   ForecasterRecursive  LGBMRegressor  ForecasterRecursive_fit   
44     ForecasterAutoreg  LGBMRegressor  ForecasterRecursive_fit   
56     ForecasterAutoreg  LGBMRegressor  ForecasterRecursive_fit   
60     ForecasterAutoreg  LGBMRegressor  ForecasterRecursive_fit   
64     ForecasterAutoreg  LGBMRegressor  ForecasterRecursive_fit   
76   ForecasterRecursive  LGBMRegressor  ForecasterRecursive_fit   
88   ForecasterRecursive  LGBMRegressor  ForecasterRecursive_fit   
100  ForecasterRecursive  LGBMRegressor  ForecasterRecursive_fit   
112  ForecasterRecursive  LGBMRegressor  ForecasterRecursive_fit   
124  ForecasterRecursive  LGBMRegressor  ForecasterRecursive_fit   
129  ForecasterRecursive  LGBMRegressor  ForecasterRecursive_fit   
144  ForecasterRecursive  LGBMRegressor  ForecasterRecursive_fit   
157  ForecasterRecursive  LGBMRegressor  ForecasterRecursive_fit   
170  ForecasterRecursive  LGBMRegressor  ForecasterRecursive_fit   
183  ForecasterRecursive  LGBMRegressor  ForecasterRecursive_fit   
196  ForecasterRecursive  LGBMRegressor  ForecasterRecursive_fit   
211  ForecasterRecursive  LGBMRegressor  ForecasterRecursive_fit   
226  ForecasterRecursive  LGBMRegressor  ForecasterRecursive_fit   
241  ForecasterRecursive  LGBMRegressor  ForecasterRecursive_fit   
256  ForecasterRecursive  LGBMRegressor  ForecasterRecursive_fit   
271  ForecasterRecursive  LGBMRegressor  ForecasterRecursive_fit   
286  ForecasterRecursive  LGBMRegressor  ForecasterRecursive_fit   
301  ForecasterRecursive  LGBMRegressor  ForecasterRecursive_fit   
307  ForecasterRecursive  LGBMRegressor  ForecasterRecursive_fit   

                        function_hash  run_time_avg  run_time_std_dev  \
8    3a6496af8f14196a05b301212de078f0      0.200046          0.021582   
20   3a6496af8f14196a05b301212de078f0      0.191685          0.046102   
32   3a6496af8f14196a05b301212de078f0      0.201174          0.040401   
44   3a6496af8f14196a05b301212de078f0      0.236430          0.039534   
56   3a6496af8f14196a05b301212de078f0      0.255430          0.060431   
60   3a6496af8f14196a05b301212de078f0      0.217465          0.029841   
64   3a6496af8f14196a05b301212de078f0      0.210943          0.030716   
76   3a6496af8f14196a05b301212de078f0      0.275427          0.034657   
88   3a6496af8f14196a05b301212de078f0      0.274136          0.074695   
100  3a6496af8f14196a05b301212de078f0      0.193109          0.022947   
112  3a6496af8f14196a05b301212de078f0      0.265002          0.047268   
124  3a6496af8f14196a05b301212de078f0      0.216749          0.036939   
129  3a6496af8f14196a05b301212de078f0      0.175987          0.009015   
144  3a6496af8f14196a05b301212de078f0      0.225332          0.037337   
157  3a6496af8f14196a05b301212de078f0      0.183055          0.014901   
170  3a6496af8f14196a05b301212de078f0      0.185623          0.028716   
183  3a6496af8f14196a05b301212de078f0      0.230508          0.062460   
196  3a6496af8f14196a05b301212de078f0      0.238670          0.035134   
211  3a6496af8f14196a05b301212de078f0      0.275120          0.072319   
226  3a6496af8f14196a05b301212de078f0      0.115473          0.008529   
241  3a6496af8f14196a05b301212de078f0      0.110754          0.011222   
256  3a6496af8f14196a05b301212de078f0      0.110432          0.012668   
271  3a6496af8f14196a05b301212de078f0      0.116359          0.013138   
286  3a6496af8f14196a05b301212de078f0      0.122203          0.009758   
301  3a6496af8f14196a05b301212de078f0      0.123325          0.005011   
307  3a6496af8f14196a05b301212de078f0      0.158533          0.050506   

                      datetime python_version skforecast_version  \
8   2025-04-23 15:05:56.608429         3.12.9             0.16.0   
20  2025-04-23 15:12:01.602347         3.12.9             0.15.1

forecaster_name regressor_name  \
9    ForecasterRecursive  LGBMRegressor   
21   ForecasterRecursive  LGBMRegressor   
33   ForecasterRecursive  LGBMRegressor   
45     ForecasterAutoreg  LGBMRegressor   
57     ForecasterAutoreg  LGBMRegressor   
61     ForecasterAutoreg  LGBMRegressor   
65     ForecasterAutoreg  LGBMRegressor   
77   ForecasterRecursive  LGBMRegressor   
89   ForecasterRecursive  LGBMRegressor   
101  ForecasterRecursive  LGBMRegressor   
113  ForecasterRecursive  LGBMRegressor   
125  ForecasterRecursive  LGBMRegressor   
130  ForecasterRecursive  LGBMRegressor   
145  ForecasterRecursive  LGBMRegressor   
158  ForecasterRecursive  LGBMRegressor   
171  ForecasterRecursive  LGBMRegressor   
184  ForecasterRecursive  LGBMRegressor   
197  ForecasterRecursive  LGBMRegressor   
212  ForecasterRecursive  LGBMRegressor   
227  ForecasterRecursive  LGBMRegressor   
242  ForecasterRecursive  LGBMRegressor   
257  ForecasterRecursive  LGBMRegressor   
272  ForecasterRecursive  LGBMRegressor   
287  ForecasterRecursive  LGBMRegressor   
302  ForecasterRecursive  LGBMRegressor   
306  ForecasterRecursive  LGBMRegressor   

                             function_name                     function_hash  \
9    ForecasterRecursive__create_train_X_y  287fbd1c4920496341a9d5f9b9a9aa2a   
21   ForecasterRecursive__create_train_X_y  287fbd1c4920496341a9d5f9b9a9aa2a   
33   ForecasterRecursive__create_train_X_y  287fbd1c4920496341a9d5f9b9a9aa2a   
45   ForecasterRecursive__create_train_X_y  287fbd1c4920496341a9d5f9b9a9aa2a   
57   ForecasterRecursive__create_train_X_y  287fbd1c4920496341a9d5f9b9a9aa2a   
61   ForecasterRecursive__create_train_X_y  1302d78676d713cc5e64125ac23a65d2   
65   ForecasterRecursive__create_train_X_y  20bdfc9de1cb7a9e99e703c087d136d3   
77   ForecasterRecursive__create_train_X_y  20bdfc9de1cb7a9e99e703c087d136d3   
89   ForecasterRecursive__create_train_X_y  20bdfc9de1cb7a9e99e703c087d136d3   
101  ForecasterRecursive__create_train_X_y  20bdfc9de1cb7a9e99e703c087d136d3   
113  ForecasterRecursive__create_train_X_y  20bdfc9de1cb7a9e99e703c087d136d3   
125  ForecasterRecursive__create_train_X_y  20bdfc9de1cb7a9e99e703c087d136d3   
130  ForecasterRecursive__create_train_X_y  20bdfc9de1cb7a9e99e703c087d136d3   
145  ForecasterRecursive__create_train_X_y  20bdfc9de1cb7a9e99e703c087d136d3   
158  ForecasterRecursive__create_train_X_y  20bdfc9de1cb7a9e99e703c087d136d3   
171  ForecasterRecursive__create_train_X_y  20bdfc9de1cb7a9e99e703c087d136d3   
184  ForecasterRecursive__create_train_X_y  20bdfc9de1cb7a9e99e703c087d136d3   
197  ForecasterRecursive__create_train_X_y  20bdfc9de1cb7a9e99e703c087d136d3   
212  ForecasterRecursive__create_train_X_y  20bdfc9de1cb7a9e99e703c087d136d3   
227  ForecasterRecursive__create_train_X_y  20bdfc9de1cb7a9e99e703c087d136d3   
242  ForecasterRecursive__create_train_X_y  20bdfc9de1cb7a9e99e703c087d136d3   
257  ForecasterRecursive__create_train_X_y  20bdfc9de1cb7a9e99e703c087d136d3   
272  ForecasterRecursive__create_train_X_y  20bdfc9de1cb7a9e99e703c087d136d3   
287  ForecasterRecursive__create_train_X_y  20bdfc9de1cb7a9e99e703c087d136d3   
302  ForecasterRecursive__create_train_X_y  20bdfc9de1cb7a9e99e703c087d136d3   
306  ForecasterRecursive__create_train_X_y  20bdfc9de1cb7a9e99e703c087d136d3   

     run_time_avg  run_time_std_dev                   datetime python_version  \
9        0.003582          0.000336 2025-04-23 15:05:58.613440         3.12.9   
21       0.002786          0.000231 2025-04-23 15:12:03.522895         3.12.9   
33       0.003637          0.000685 2025-04-23 15:15:59.144846         3.12.9   
45            NaN               NaN 2025-04-23 15:31:32.335009         3.12.9   
57            NaN               NaN 2025-04-23 15:41:06.200461         3.12.9   
61            NaN               NaN 2025-04-23 15:46:07.619566         3.12.9   
65       0.003645          0.000583 2025-04-23 15:46:40.854571         3.12.9   
77       0.004178          0.000579 20

forecaster_name regressor_name                function_name  \
10   ForecasterRecursive  LGBMRegressor  ForecasterRecursive_predict   
22   ForecasterRecursive  LGBMRegressor  ForecasterRecursive_predict   
34   ForecasterRecursive  LGBMRegressor  ForecasterRecursive_predict   
46     ForecasterAutoreg  LGBMRegressor  ForecasterRecursive_predict   
58     ForecasterAutoreg  LGBMRegressor  ForecasterRecursive_predict   
62     ForecasterAutoreg  LGBMRegressor  ForecasterRecursive_predict   
66     ForecasterAutoreg  LGBMRegressor  ForecasterRecursive_predict   
78   ForecasterRecursive  LGBMRegressor  ForecasterRecursive_predict   
90   ForecasterRecursive  LGBMRegressor  ForecasterRecursive_predict   
102  ForecasterRecursive  LGBMRegressor  ForecasterRecursive_predict   
114  ForecasterRecursive  LGBMRegressor  ForecasterRecursive_predict   
126  ForecasterRecursive  LGBMRegressor  ForecasterRecursive_predict   
131  ForecasterRecursive  LGBMRegressor  ForecasterRecursive_predict   
146  ForecasterRecursive  LGBMRegressor  ForecasterRecursive_predict   
159  ForecasterRecursive  LGBMRegressor  ForecasterRecursive_predict   
172  ForecasterRecursive  LGBMRegressor  ForecasterRecursive_predict   
185  ForecasterRecursive  LGBMRegressor  ForecasterRecursive_predict   
198  ForecasterRecursive  LGBMRegressor  ForecasterRecursive_predict   
213  ForecasterRecursive  LGBMRegressor  ForecasterRecursive_predict   
228  ForecasterRecursive  LGBMRegressor  ForecasterRecursive_predict   
243  ForecasterRecursive  LGBMRegressor  ForecasterRecursive_predict   
258  ForecasterRecursive  LGBMRegressor  ForecasterRecursive_predict   
273  ForecasterRecursive  LGBMRegressor  ForecasterRecursive_predict   
288  ForecasterRecursive  LGBMRegressor  ForecasterRecursive_predict   
303  ForecasterRecursive  LGBMRegressor  ForecasterRecursive_predict   
308  ForecasterRecursive  LGBMRegressor  ForecasterRecursive_predict   

                        function_hash  run_time_avg  run_time_std_dev  \
10   4f8ae3116340ac90eb9e66eac42789de      0.075136          0.004202   
22   4f8ae3116340ac90eb9e66eac42789de      0.058053          0.001119   
34   4f8ae3116340ac90eb9e66eac42789de      0.084377          0.019527   
46   4f8ae3116340ac90eb9e66eac42789de      0.075075          0.003942   
58   4f8ae3116340ac90eb9e66eac42789de      0.080083          0.004092   
62   4f8ae3116340ac90eb9e66eac42789de      0.068110          0.005326   
66   4f8ae3116340ac90eb9e66eac42789de      0.068882          0.004036   
78   4f8ae3116340ac90eb9e66eac42789de      0.089361          0.006090   
90   4f8ae3116340ac90eb9e66eac42789de      0.077495          0.007502   
102  4f8ae3116340ac90eb9e66eac42789de      0.061347          0.002380   
114  4f8ae3116340ac90eb9e66eac42789de      0.099835          0.025446   
126  4f8ae3116340ac90eb9e66eac42789de      0.074483          0.005089   
131  4f8ae3116340ac90eb9e66eac42789de      0.059138          0.002952   
146  4f8ae3116340ac90eb9e66eac42789de      0.075335          0.004613   
159  4f8ae3116340ac90eb9e66eac42789de      0.056943          0.001530   
172  4f8ae3116340ac90eb9e66eac42789de      0.057730          0.000908   
185  4f8ae3116340ac90eb9e66eac42789de      0.060702          0.001503   
198  4f8ae3116340ac90eb9e66eac42789de      0.072572          0.002594   
213  4f8ae3116340ac90eb9e66eac42789de      0.086275          0.011340   
228  4f8ae3116340ac90eb9e66eac42789de      0.045880          0.004895   
243  4f8ae3116340ac90eb9e66eac42789de      0.049741          0.005705   
258  4f8ae3116340ac90eb9e66eac42789de      0.049121          0.005243   
273  4f8ae3116340ac90eb9e66eac42789de      0.047233          0.003683   
288  4f8ae3116340ac90eb9e66eac42789de      0.057668          0.007389   
303  4f8ae3116340ac90eb9e66eac42789de      0.055124          0.004537   
308  4f8ae3116340ac90eb9e66eac42789de      0.058437          0.005536   

                      datetime python_version skforecast_version  \
10  2025-04-23 15:05:58.

forecaster_name regressor_name  \
11   ForecasterRecursive  LGBMRegressor   
23   ForecasterRecursive  LGBMRegressor   
35   ForecasterRecursive  LGBMRegressor   
47     ForecasterAutoreg  LGBMRegressor   
59     ForecasterAutoreg  LGBMRegressor   
63     ForecasterAutoreg  LGBMRegressor   
67     ForecasterAutoreg  LGBMRegressor   
79   ForecasterRecursive  LGBMRegressor   
91   ForecasterRecursive  LGBMRegressor   
103  ForecasterRecursive  LGBMRegressor   
115  ForecasterRecursive  LGBMRegressor   
127  ForecasterRecursive  LGBMRegressor   
132  ForecasterRecursive  LGBMRegressor   
147  ForecasterRecursive  LGBMRegressor   
160  ForecasterRecursive  LGBMRegressor   
173  ForecasterRecursive  LGBMRegressor   
186  ForecasterRecursive  LGBMRegressor   
199  ForecasterRecursive  LGBMRegressor   
214  ForecasterRecursive  LGBMRegressor   
229  ForecasterRecursive  LGBMRegressor   
244  ForecasterRecursive  LGBMRegressor   
259  ForecasterRecursive  LGBMRegressor   
274  ForecasterRecursive  LGBMRegressor   
289  ForecasterRecursive  LGBMRegressor   
304  ForecasterRecursive  LGBMRegressor   
309  ForecasterRecursive  LGBMRegressor   

                                  function_name  \
11   ForecasterRecursive__create_predict_inputs   
23   ForecasterRecursive__create_predict_inputs   
35   ForecasterRecursive__create_predict_inputs   
47   ForecasterRecursive__create_predict_inputs   
59   ForecasterRecursive__create_predict_inputs   
63   ForecasterRecursive__create_predict_inputs   
67   ForecasterRecursive__create_predict_inputs   
79   ForecasterRecursive__create_predict_inputs   
91   ForecasterRecursive__create_predict_inputs   
103  ForecasterRecursive__create_predict_inputs   
115  ForecasterRecursive__create_predict_inputs   
127  ForecasterRecursive__create_predict_inputs   
132  ForecasterRecursive__create_predict_inputs   
147  ForecasterRecursive__create_predict_inputs   
160  ForecasterRecursive__create_predict_inputs   
173  ForecasterRecursive__create_predict_inputs   
186  ForecasterRecursive__create_predict_inputs   
199  ForecasterRecursive__create_predict_inputs   
214  ForecasterRecursive__create_predict_inputs   
229  ForecasterRecursive__create_predict_inputs   
244  ForecasterRecursive__create_predict_inputs   
259  ForecasterRecursive__create_predict_inputs   
274  ForecasterRecursive__create_predict_inputs   
289  ForecasterRecursive__create_predict_inputs   
304  ForecasterRecursive__create_predict_inputs   
309  ForecasterRecursive__create_predict_inputs   

                        function_hash  run_time_avg  run_time_std_dev  \
11   0f4a625e8b1bb7e3f0c5bb77a04cc2fb      0.002528          0.000266   
23   0f4a625e8b1bb7e3f0c5bb77a04cc2fb      0.002659          0.000322   
35   0f4a625e8b1bb7e3f0c5bb77a04cc2fb      0.003698          0.000622   
47   0f4a625e8b1bb7e3f0c5bb77a04cc2fb           NaN               NaN   
59   0f4a625e8b1bb7e3f0c5bb77a04cc2fb           NaN               NaN   
63   0f4a625e8b1bb7e3f0c5bb77a04cc2fb           NaN               NaN   
67   0f4a625e8b1bb7e3f0c5bb77a04cc2fb           NaN               NaN   
79   0f4a625e8b1bb7e3f0c5bb77a04cc2fb      0.003530          0.000365   
91   0f4a625e8b1bb7e3f0c5bb77a04cc2fb      0.003004          0.000305   
103  0f4a625e8b1bb7e3f0c5bb77a04cc2fb      0.002960          0.000349   
115  0f4a625e8b1bb7e3f0c5bb77a04cc2fb      0.002492          0.000286   
127  0f4a625e8b1bb7e3f0c5bb77a04cc2fb      0.002464          0.000214   
132  0f4a625e8b1bb7e3f0c5bb77a04cc2fb      0.002063          0.000222   
147  0f4a625e8b1bb7e3f0c5bb77a04cc2fb      0.002423          0.000211   
160  0f4a625e8b1bb7e3f0c5bb77a04cc2fb      0.002517          0.000247   
173  0f4a625e8b1bb7e3f0c5bb77a04cc2fb      0.002665          0.000241   
186  0f4a625e8b1bb7e3f0c5bb77a04cc2fb      0.002630          0.000187   
199  0f4a625e8b1bb7e3f0c5bb77a04cc2fb      0.003271          0.000473   
214  0f4a625e8b1bb7e3f0c5bb77a04cc2fb      0.002464          0.000202   
229  0f4a

forecaster_name regressor_name                    function_name  \
200  ForecasterRecursive  LGBMRegressor  ForecasterRecursive_backtesting   
215  ForecasterRecursive  LGBMRegressor  ForecasterRecursive_backtesting   
230  ForecasterRecursive  LGBMRegressor  ForecasterRecursive_backtesting   
245  ForecasterRecursive  LGBMRegressor  ForecasterRecursive_backtesting   
260  ForecasterRecursive  LGBMRegressor  ForecasterRecursive_backtesting   
275  ForecasterRecursive  LGBMRegressor  ForecasterRecursive_backtesting   
290  ForecasterRecursive  LGBMRegressor  ForecasterRecursive_backtesting   
305  ForecasterRecursive  LGBMRegressor  ForecasterRecursive_backtesting   
310  ForecasterRecursive  LGBMRegressor  ForecasterRecursive_backtesting   

                        function_hash  run_time_avg  run_time_std_dev  \
200  dad167768fbdc53eca10d293c5861956      0.920042          0.154116   
215  dad167768fbdc53eca10d293c5861956      0.823157          0.042117   
230  dad167768fbdc53eca10d293c5861956      0.483836          0.014478   
245  dad167768fbdc53eca10d293c5861956      0.487309          0.014333   
260  dad167768fbdc53eca10d293c5861956      0.478833          0.020217   
275  dad167768fbdc53eca10d293c5861956      0.515136          0.027150   
290  dad167768fbdc53eca10d293c5861956      0.578477          0.010353   
305  dad167768fbdc53eca10d293c5861956      0.582918          0.009795   
310  dad167768fbdc53eca10d293c5861956      0.642805          0.039951   

                      datetime python_version skforecast_version  \
200 2025-04-23 22:51:18.980518         3.12.9             0.14.0   
215 2025-04-23 22:59:16.873858         3.12.9             0.16.0   
230 2025-04-24 10:30:38.539449        3.11.10             0.16.0   
245 2025-04-24 10:38:50.414649        3.11.10             0.15.1   
260 2025-04-24 10:44:55.867188        3.11.10             0.14.0   
275 2025-04-24 11:12:12.221550        3.11.10             0.14.0   
290 2025-04-24 11:22:10.983319        3.11.10             0.15.1   
305 2025-04-24 11:35:21.783602        3.11.10             0.16.0   
310 2025-04-24 12:19:09.013185        3.11.10             0.16.0   

    numpy_version pandas_version sklearn_version lightgbm_version  \
200         2.2.5          2.2.3           1.6.1            4.6.0   
215         2.2.5          2.2.3           1.6.1            4.6.0   
230         2.1.3          2.2.3           1.6.1            4.5.0   
245         2.1.3          2.2.3           1.6.1            4.5.0   
260         2.1.3          2.2.3           1.6.1            4.5.0   
275         2.1.3          2.2.3           1.6.1            4.5.0   
290         2.1.3          2.2.3           1.6.1            4.5.0   
305         2.1.3          2.2.3           1.6.1            4.5.0   
310         2.2.5          2.2.3           1.6.1            4.5.0   

                                          platform  \
200  Linux-6.11.0-21-generic-x86_64-with-glibc2.39   
215  Linux-6.11.0-21-generic-x86_64-with-glibc2.39   
230                      Windows-10-10.0.19045-SP0   
245                      Windows-10-10.0.19045-SP0   
260                      Windows-10-10.0.19045-SP0   
275                      Windows-10-10.0.19045-SP0   
290                      Windows-10-10.0.19045-SP0   
305                      Windows-10-10.0.19045-SP0   
310                      Windows-10-10.0.19045-SP0   

                                             processor  cpu_count  memory_gb  
200                                             x86_64          8      16.64  
215                                             x86_64          8      16.64  
230  Intel64 Family 6 Model 141 Stepping 1, Genuine...         16      34.07  
245  Intel64 Family 6 Model 141 Stepping 1, Genuine...         16      34.07  
260  Intel64 Family 6 Model 141 Stepping 1, Genuine...         16      34.07  
275  Intel64 Family 6 Model 141 Stepping 1, Genuine...         16      34.07  
290  Intel64 Family 6 Model 141 Stepping 1, Genuine

# Summary of historical results

In [13]:
results_benchmark_all = joblib.load("./benchmark.joblib")
results_benchmark_all['function_name'] = results_benchmark_all['function_name'].str.split('_', n=1).str[1]
results_benchmark_all = results_benchmark_all.groupby(['forecaster_name', 'skforecast_version', 'function_name'])['run_time_avg'].agg('median').reset_index()
results_benchmark_all = results_benchmark_all.sort_values(by=['function_name'])

fig = px.bar(
    results_benchmark_all.query("forecaster_name in ['ForecasterRecursiveMultiSeries', 'ForecasterAutoregMultiSeries']"),
    x='function_name',
    y='run_time_avg',
    color='skforecast_version',
    barmode='group',
    title='MultiSeries Forecasters - Median Run Time by Function and skforecast Version',
    labels={'run_time_avg': 'Median Run Time (s)', 'function_name': 'Function'},
    category_orders={'skforecast_version': sorted(results_benchmark_all['skforecast_version'].unique())}
)
fig.update_layout(xaxis_tickangle=-45)
fig.show()

fig = px.bar(
    results_benchmark_all.query("forecaster_name in ['ForecasterRecursive', 'ForecasterAutoreg']"),
    x='function_name',
    y='run_time_avg',
    color='skforecast_version',
    barmode='group',
    title='Single-Series Forecasters - Median Run Time by Function and skforecast Version',
    labels={'run_time_avg': 'Median Run Time (s)', 'function_name': 'Function'},
    category_orders={'skforecast_version': sorted(results_benchmark_all['skforecast_version'].unique())}
)
fig.update_layout(xaxis_tickangle=-45)
fig.show()
